In [ ]:
# -*- coding: utf-8 -*-

import os
import nsq
import time
import json
import argparse
import logging
import subprocess
import jieba
import jieba.analyse
from bson import ObjectId
from config import policy_db, JAR_PATH, APK_TMP, APK_JSON_TMP


def handler(message):
    body = message.body
    logging.info('raw msg: %s'.format(body))

    try:
        data = json.loads(body)
    except Exception as ex:
        print ex

    # path = "/Users/saggev/Downloads/eb32203189a8efba19cb1c85b7401e65.apk"
    # policy = "我的手机地址"
    #db.policy_apps
    if not os.path.exists(data["app"]):
        print "apk 路径不存在"
    try:
        analysis = PrivacyAnalysis(data["app"], data["policy"], data["apps_id"])
        result = analysis()

        item = policy_db.policy_apps.find_one({
            "_id": ObjectId(data['apps_id'])})
        if item:
            policy_db.policy_apps.update_one({
                "_id": ObjectId(data['apps_id'])}, {"$set": result})
    except Exception as ex:
        print ex

    return True


class PrivacyAnalysis():
    def __init__(self, apkpath, policy, apps_id):
        self.apkpath = apkpath
        self.policy = policy
        self.apps_id = apps_id
        self.synonyms = list()
        if not os.path.exists(apkpath):
            print "apk 路径不存在"
            
    #load synonyms
    #db.policy_privacy
    def init_synonyms(self):
        self.synonyms = []
        for ele in policy_db.policy_privacy.find():
            self.synonyms.append({"root": ele['root'], "slist": ele["slist"]})            
                

    def privacy_analysis(self, strings):
        strings_list = jieba.cut(strings)

        privacy_words = []
        for item in strings_list:
            for ele in self.synonyms:
                if item in ele["slist"]:
                    if ele['root'] not in privacy_words:
                        privacy_words.append(ele["root"])

        return privacy_words



    def get_apk_info(self):
        res_json = APK_JSON_TMP + self.apkpath.split("/")[-1].split(".apk")[0] + ".json"
        if os.path.exists(res_json):
            os.remove(res_json)
            os.mknod(res_json)
        else:
            os.mknod(res_json)

        stdout = subprocess.Popen(["java -jar {}aig_jni.jar -bsr {} {}".format(
            JAR_PATH, self.apkpath, res_json)], stdout=subprocess.PIPE, shell=True)
        stdout.communicate(input=None)

        try:
            ofile = open(res_json, "r")
            data = json.load(ofile)
        except Exception as ex:
            print ex

        info = dict()
        info['package'] = data["basic"].get("package", "")
        info['version'] = data["basic"].get("version", "")
        info['sha1'] = data["basic"].get("sha1", "")
        info['appname'] = data["basic"].get("appname", "")
        info['img'] = data["basic"].get("img", "")
        info['version'] = data["basic"].get("version", "")
        info['size'] = data['basic'].get("filesize", "")
        info['md5'] = data['basic'].get("md5", "")
        info["path"] = data["basic"].get("filepath", "")
        info['sha256'] = data['basic'].get("sha256", "")
        info['string'] = data['string']

        ofile.close()
        os.remove(res_json)
        return info
    
    #db.analysis_status
    def update_status(self, _id, keyword):
        policy_db.analysis_status.update_one({"_id": _id}, {"$set": {"status": keyword}})

    def __call__(self):
        one = policy_db.analysis_status.insert_one({"apps_id": self.apps_id, "status": "starting"})
        res_id = one.inserted_id

        self.update_status(res_id, "get_apk_info")
        appinfo = self.get_apk_info()

        self.update_status(res_id, "init_keyword")
        self.init_synonyms()

        app_strings = ""
        for ele in appinfo['string'].keys():
            for item in appinfo['string'][ele]:
                if len(item) == 0:
                    continue
                app_strings += item + "\n"

        result = dict()
        self.update_status(res_id, "policy_privacy_analysis")
        result['policy_privacy_keyword'] = self.privacy_analysis(self.policy)

        self.update_status(res_id, "app_privacy_analysis")
        result["app_privacy_keyword"] = self.privacy_analysis(app_strings)

        del appinfo['string']
        result["apkinfo"] = appinfo
        self.update_status(res_id, "end")

        return result


if __name__ == "__main__":
    parser = argparse.ArgumentParser(description='')
    parser.add_argument('-topic', action="store", type=str, default="app_analysis")
    args = parser.parse_args()
    topic = args.topic

    print("Starting...............")

    r = nsq.Reader(
        message_handler=handler,
        nsqd_tcp_addresses=['127.0.0.1:4150'],
        topic=topic,
        channel=topic+"_channel",
        lookupd_poll_interval=15)

    nsq.run()


In [22]:
import jieba

s1 = jieba.cut("支付账号")
print( "/ ".join(s1))

支付/ 账号


In [ ]:
import gensim
from gensim.models import Word2Vec

model = gensim.models.Word2Vec.load('C:/Users/aiya/Desktop/3files/embedding.bin')
s1 = model.most_similar('起点',topn=20)
print (s1)
#model = gensim.models.KeyedVectors.load_word2vec_format('C:/Users/aiya/Desktop/3files/embedding.bin', binary=False)

c:\users\aiya\appdata\local\programs\python\python36\lib\site-packages\gensim\utils.py:1212: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [13]:
import gensim
from gensim.models import KeyedVectors
wv_from_text = KeyedVectors.load_word2vec_format('C:/Users/aiya/Desktop/3files/embeddings.bin', binary=False)

ValueError: invalid literal for int() with base 10: '，'

In [27]:
import json
with open("C:/Users/aiya/Desktop/data/literal/1.json", "r") as frh:
    for line in frh:
        string_collection = json.load(frh)#list
    
        str_map = string_collection[0]["string"] #dict
        print (str_map)
        print (type(str_map))
        for k in str_map.keys():
            for str in str_map[k]:
                print (str)

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [2]:
from sklearn.decomposition import IncrementalPCA    # inital reduction
from sklearn.manifold import TSNE                   # final reduction

import numpy as np                                  # array handling

from plotly.offline import init_notebook_mode, iplot, plot
import plotly.graph_objs as go

import gensim
from gensim.models import Word2Vec

import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

model = gensim.models.Word2Vec.load("C:/Users/aiya/Desktop/policy_model.bin")

def reduce_dimensions(model, plot_in_notebook = True):

    num_dimensions = 2  

    vectors = []        # positions in vector space
    labels = []         # keep track of words to label our data again later
    for word in model.wv.vocab:
        vectors.append(model[word])#vector
        labels.append(word) #words

    # convert both lists into numpy vectors for reduction
    vectors = np.asarray(vectors)
    labels = np.asarray(labels)
    
    # reduce using t-SNE
    vectors = np.asarray(vectors)
    logging.info('starting tSNE dimensionality reduction. This may take some time.')
    tsne = TSNE(n_components=num_dimensions, random_state=0)
    vectors = tsne.fit_transform(vectors)

    x_vals = [v[0] for v in vectors]
    y_vals = [v[1] for v in vectors]
        
    # Create a trace
    trace = go.Scatter(
        x=x_vals,
        y=y_vals,
        mode='text',
        text=labels
        )
    
    data = [trace]
    
    logging.info('All done. Plotting.')
    
    if plot_in_notebook:
        init_notebook_mode(connected=True)
        iplot(data, filename='word-embedding-plot')

if __name__ == "__main__":
    reduce_dimensions(model)        

c:\users\aiya\appdata\local\programs\python\python36\lib\site-packages\gensim\utils.py:1212: UserWarning:

detected Windows; aliasing chunkize to chunkize_serial

2019-02-20 15:34:08,433 : INFO : loading Word2Vec object from C:/Users/aiya/Desktop/policy_model.bin
2019-02-20 15:34:08,551 : INFO : loading wv recursively from C:/Users/aiya/Desktop/policy_model.bin.wv.* with mmap=None
2019-02-20 15:34:08,555 : INFO : setting ignored attribute vectors_norm to None
2019-02-20 15:34:08,560 : INFO : loading trainables recursively from C:/Users/aiya/Desktop/policy_model.bin.trainables.* with mmap=None
2019-02-20 15:34:08,563 : INFO : loading vocabulary recursively from C:/Users/aiya/Desktop/policy_model.bin.vocabulary.* with mmap=None
2019-02-20 15:34:08,578 : INFO : setting ignored attribute cum_table to None
2019-02-20 15:34:08,585 : INFO : loaded C:/Users/aiya/Desktop/policy_model.bin
c:\users\aiya\appdata\local\programs\python\python36\lib\site-packages\ipykernel_launcher.py:24: Deprecation

In [8]:
import gensim
from gensim.models import Word2Vec

model_with_loss = gensim.models.Word2Vec(sentences, min_count=1, compute_loss=True)
#model = gensim.models.Word2Vec.load("C:/Users/aiya/Desktop/policy_model.bin")
# getting the training loss value
training_loss = model.get_latest_training_loss()
print(training_loss)

#wrong

NameError: name 'sentences' is not defined

In [19]:
import numpy as np
from gensim.models import Word2Vec


model = Word2Vec.load("C:/Users/aiya/Desktop/policy_model.bin")

word2idx = {"_PAD": 0} # 初始化 `[word : token]` 字典，后期 tokenize 语料库就是用该词典。

vocab_list = [(k, model.wv[k]) for k, v in model.wv.vocab.items()]

# 存储所有 word2vec 中所有向量的数组，留意其中多一位，词向量全为 0， 用于 padding
embeddings_matrix = np.zeros((len(model.wv.vocab.items()) + 1, model.vector_size))
for i in range(len(vocab_list)):
    word = vocab_list[i][0]
    word2idx[word] = i + 1
    embeddings_matrix[i + 1] = vocab_list[i][1]

from keras.layers import Embedding

EMBEDDING_DIM = 100 #词向量维度

embedding_layer = Embedding(len(embeddings_matrix),
                            EMBEDDING_DIM,
                            weights=[embeddings_matrix],
                            trainable=False)

2019-02-20 17:31:49,111 : INFO : loading Word2Vec object from C:/Users/aiya/Desktop/policy_model.bin
2019-02-20 17:31:50,652 : INFO : loading wv recursively from C:/Users/aiya/Desktop/policy_model.bin.wv.* with mmap=None
2019-02-20 17:31:50,694 : INFO : setting ignored attribute vectors_norm to None
2019-02-20 17:31:50,845 : INFO : loading trainables recursively from C:/Users/aiya/Desktop/policy_model.bin.trainables.* with mmap=None
2019-02-20 17:31:50,870 : INFO : loading vocabulary recursively from C:/Users/aiya/Desktop/policy_model.bin.vocabulary.* with mmap=None
2019-02-20 17:31:50,873 : INFO : setting ignored attribute cum_table to None
2019-02-20 17:31:50,876 : INFO : loaded C:/Users/aiya/Desktop/policy_model.bin


ImportError: cannot import name 'Network'

In [24]:
#https://eliyar.biz/using-pre-trained-gensim-word2vector-in-a-keras-model-and-visualizing/
import json

f = open("C:/Users/aiya/Desktop/1.json",'r',encoding='utf-8')
ln = 0
for line in f.readlines():
    dic = json.loads(line,encoding='utf-8')
f.close()

[{'string': {'assets/configs.xml': ['1', '1.0', '<?xml version=', 'UTF-8', '>\r\n\t\t<sdkid>47</sdkid>\r\n\t\t<channelid>7000</channelid>\r\n\t\t<channelid_sub>7001</channelid_sub>\r\n\t\t<gameid>6</gameid>\r\n\t\t<cpid>1</cpid>\r\n\t\t<updateurl>http://shenmoversion1.01234.com.cn:9090/shenmo/android/</updateurl> \r\n\t\t<updateurl2>http://117.121.29.5:9090/shenmo/android/</updateurl2>\r\n\t\t<pushurl>http://shenmopush.01234.com.cn:8000</pushurl>\r\n\t\t<noticeurl>http://shenmonotice.01234.com.cn:9090</noticeurl>\r\n\t\t<releaseversion>2</releaseversion>\r\n\t</config>\r\n</configs>\r\nq`', '?>\r\n<configs>\r\n\t<config id=', ' encoding='], 'lib/mips/libhellocpp.so': ['setObjects', '', '\x01', '\x02', '\x03', 'half', 'clampf', '\x04', '\x05', ' Write', 'ccg', 'kCCHTTPRequestAcceptEncodingDeflate', '\x06', '\x07', '\x08', 'CCTMXMapInfo', 'kmGLGetMatrix', '\t', '\n', '\x0b', '\x0c', 'childs', '\r', '\x0e', '\x0f', '\x10', 'ccp', 'N7cocos2d9CCScaleToE', '\x11', '\x12', "Blank needed after

In [38]:
#!/usr/bin/python
# -*- coding:utf-8 -*-

import os
import json
import string
import sys
import gensim
from gensim.models import Word2Vec
#from smart_open import smart_open
import logging
import re
#import langid
import jieba
#from Crypto.SelfTest.Random.test__UserFriendlyRNG import multiprocessing
import io
import multiprocessing


class embedding(object):
    def __init__(self, stop_words_path):
        #import importlib python3
        #importlib.reload(sys) python3
        import sys
        reload(sys)
        sys.setdefaultencoding('utf-8')
        self.stopwords_path = stop_words_path
        self.model = None
        self.sentences_count = 0
        self.file_count = 0
        self.none_chinese_file = 0
        logging.basicConfig(level = logging.INFO,format = '%(asctime)s - %(name)s - %(levelname)s - %(message)s')
        pass

    def _is_chinese(self, sentence):
        for ch in sentence:#sentence.decode('utf-8')
            if u'\u4e00' <= ch <= u'\u9fff':
                return True
        return False

    def show_static_data(self):
        print("Total {} sentences".format(self.sentences_count))
        print("Total {} files".format(self.file_count))
        print("Total {} NONE chinese files".format(self.none_chinese_file))

        with open("./log.log", "a") as fwh:
            fwh.write("Total {} sentences\n".format(self.sentences_count))
            fwh.write("Total {} files\n".format(self.file_count))
            fwh.write("Total {} NONE chinese files\n".format(self.none_chinese_file))

    def _gen_model(self, model_path, sentences_collection):
        if os.path.isfile(model_path):
            self.model = Word2Vec.load(model_path)
            self.model.build_vocab(sentences_collection, update = True)
        else:
            self.model = Word2Vec(sentences_collection, min_count = 1, workers = multiprocessing.cpu_count()-2)
        self.model.train(sentences_collection, total_examples=len(sentences_collection), epochs=self.model.iter)

        if self.model != None:
            self.model.save(model_path)
        return

    def gen_model(self, copus_path, back_up, model_path):
        stopwords = [line.strip() for line in io.open(self.stopwords_path, 'r', encoding='utf-8').readlines()]
        sentences_collection = []

        for dirpath, dirnames, filenames in os.walk(copus_path):
            for filename in filenames:
                f = os.path.join(dirpath, filename)
                #print ((" - processing {} file: {}").format(self.file_count, f)) python3
                print (" - processing {} file: {}").format(self.file_count, f)
                result = None
            
                try:
                    str_collection = json.load(io.open(f, 'r', encoding='utf-8'))
                    str_map = str_collection[0]["string"]
                except:
                    print ((" - err in processing {} file: {}").format(self.file_count, f))
                    continue
                   
                #str_collection = json.load(io.open(f, 'r', encoding='utf-8'))
                #print (type(str_collection))
                #str_map = str_collection[0]["string"]
                sentences = []
                for k in str_map.keys():
                    for str in str_map[k]:
                        if self._is_chinese(str):
                            my_re = '[a-zA-Z0-9’!"#$%&\'()*+,-./:;<=>?@，。?★、…【】《》？“”‘’！[\\]^_`{|}~\n]+'
                            clean_sentence = re.sub(my_re, "", str)

                            seg_data = jieba.cut(clean_sentence, cut_all = True)    # I am preferred to use True

                            clean_list = [i for i in seg_data if i not in stopwords]
                            clean_list = list(filter(None, clean_list))#filter(None, clean_list)
#                         print clean_sentence
#                         for i in clean_list:
#                             print i
#                         print clean_list
                            if len(clean_list) == 0:
                                continue
                            sentences.append(clean_list)

                            self.sentences_count += 1

                self.file_count += 1
                if len(sentences) == 0:
                    self.none_chinese_file += 1
                else:
                    sentences_collection += sentences  #do NOT use append
                # in case of crashing
                if self.file_count % 5000 == 0 and len(sentences_collection) != 0: # load is time consuming
                    self._gen_model(model_path, sentences_collection)
                    sentences_collection = []

                os.system("mv \"{}\" \"{}\"".format(f, back_up))    # so I can catch err

        if len(sentences_collection) != 0:
            self._gen_model(model_path, sentences_collection)
        return

if __name__ == "__main__":

    # https://www.jianshu.com/p/5f04e97d1b27
# model.save_word2vec_format('/tmp/mymodel.txt',binary=False)
    print "**** start ****"
    myEmbedding = embedding("C:/Users/aiya/Desktop/data/stopwords_chs.txt")
    myEmbedding.gen_model("C:/Users/aiya/Desktop/data/literal", "C:/Users/aiya/Desktop/data/corpus_bak", "C:/Users/aiya/Desktop/janus_chs_model")
    myEmbedding.show_static_data()

# 电子邮件
# 电子
# 新邮件
# 电子书
# 电子邮箱
# 子书
# 新邮
# 帐户
# 邮箱
# 发送到
#     model = gensim.models.Word2Vec.load("./model")
#     for v in model.most_similar(positive=[u'生日'], topn=20):
#         print v[0]
    print "**** done *****"


**** start ****
 - processing 0 file: C:/Users/aiya/Desktop/data/literal\1.json
<class 'list'>


2019-02-21 14:07:50,555 - gensim.models.word2vec - INFO - collecting all words and their counts
2019-02-21 14:07:50,563 - gensim.models.word2vec - INFO - PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2019-02-21 14:07:50,578 - gensim.models.word2vec - INFO - collected 797 word types from a corpus of 4475 raw words and 1109 sentences
2019-02-21 14:07:50,588 - gensim.models.word2vec - INFO - Loading a fresh vocabulary
2019-02-21 14:07:50,615 - gensim.models.word2vec - INFO - effective_min_count=1 retains 797 unique words (100% of original 797, drops 0)
2019-02-21 14:07:50,620 - gensim.models.word2vec - INFO - effective_min_count=1 leaves 4475 word corpus (100% of original 4475, drops 0)
2019-02-21 14:07:50,640 - gensim.models.word2vec - INFO - deleting the raw counts dictionary of 797 items
2019-02-21 14:07:50,644 - gensim.models.word2vec - INFO - sample=0.001 downsamples 88 most-common words
2019-02-21 14:07:50,648 - gensim.models.word2vec - INFO - downsampling leaves

Total 1109 sentences
Total 1 files
Total 0 NONE chinese files
**** done *****


In [41]:
model = gensim.models.Word2Vec.load("C:/Users/aiya/Desktop/janus_chs_model")
for v in model.most_similar(positive=[u'账户'], topn=20):
    print (v[0])

2019-02-21 14:11:21,805 - gensim.utils - INFO - loading Word2Vec object from C:/Users/aiya/Desktop/janus_chs_model
2019-02-21 14:11:21,858 - gensim.utils - INFO - loading wv recursively from C:/Users/aiya/Desktop/janus_chs_model.wv.* with mmap=None
2019-02-21 14:11:21,895 - gensim.utils - INFO - setting ignored attribute vectors_norm to None
2019-02-21 14:11:21,896 - gensim.utils - INFO - loading vocabulary recursively from C:/Users/aiya/Desktop/janus_chs_model.vocabulary.* with mmap=None
2019-02-21 14:11:21,899 - gensim.utils - INFO - loading trainables recursively from C:/Users/aiya/Desktop/janus_chs_model.trainables.* with mmap=None
2019-02-21 14:11:21,900 - gensim.utils - INFO - setting ignored attribute cum_table to None
2019-02-21 14:11:21,901 - gensim.utils - INFO - loaded C:/Users/aiya/Desktop/janus_chs_model
c:\users\aiya\appdata\local\programs\python\python36\lib\site-packages\ipykernel_launcher.py:2: DeprecationWarning: Call to deprecated `most_similar` (Method will be remov

请
输入
百度
手机
账号
填写
密码
游戏
支付
银行
余额
建议
网络
信息
卡
数字
错误
版本
手机号
绑定


In [42]:
model["帐号"]

c:\users\aiya\appdata\local\programs\python\python36\lib\site-packages\ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  """Entry point for launching an IPython kernel.


array([-3.19531513e-03,  5.59891760e-03,  3.60690174e-03, -2.80505177e-02,
        4.50849859e-03, -2.70963483e-03, -2.59679891e-02, -3.22603085e-03,
       -9.47744958e-03,  3.04782321e-03, -2.65931264e-02,  1.05596818e-02,
       -1.33923311e-02, -1.03550078e-02,  6.53673336e-03,  4.60768970e-05,
       -3.52771650e-03,  8.02673958e-03, -2.15702783e-02, -1.37356576e-03,
       -8.84749182e-03, -7.08030630e-03,  2.03792546e-02,  6.69139577e-03,
        7.19679007e-03,  2.21338193e-03,  4.74775210e-03, -7.82160030e-04,
        2.20543835e-02, -2.49907770e-03, -1.16742505e-02, -2.49545486e-03,
        5.55609213e-03, -4.62182797e-03, -8.63107573e-03,  1.83254306e-03,
       -3.23062693e-03,  4.66080057e-03, -2.99704857e-02, -2.04075947e-02,
        2.12541483e-02, -1.29909515e-02, -3.76572437e-03,  5.80153801e-03,
       -1.28541968e-03, -7.47566752e-04,  1.46990297e-02,  5.35797328e-03,
        1.07610747e-02,  7.84114003e-03, -1.27013503e-02, -4.29614540e-03,
       -1.60371941e-02, -

In [44]:
import numpy as np
from gensim.models import Word2Vec


model = Word2Vec.load("C:/Users/aiya/Desktop/janus_chs_model")

word2idx = {"_PAD": 0} # 初始化 `[word : token]` 字典，后期 tokenize 语料库就是用该词典。

vocab_list = [(k, model.wv[k]) for k, v in model.wv.vocab.items()]

# 存储所有 word2vec 中所有向量的数组，留意其中多一位，词向量全为 0， 用于 padding
embeddings_matrix = np.zeros((len(model.wv.vocab.items()) + 1, model.vector_size))
for i in range(len(vocab_list)):
    word = vocab_list[i][0]
    word2idx[word] = i + 1
    embeddings_matrix[i + 1] = vocab_list[i][1]



2019-02-21 16:04:53,939 - gensim.utils - INFO - loading Word2Vec object from C:/Users/aiya/Desktop/janus_chs_model
2019-02-21 16:04:57,001 - gensim.utils - INFO - loading wv recursively from C:/Users/aiya/Desktop/janus_chs_model.wv.* with mmap=None
2019-02-21 16:04:57,028 - gensim.utils - INFO - setting ignored attribute vectors_norm to None
2019-02-21 16:04:57,141 - gensim.utils - INFO - loading vocabulary recursively from C:/Users/aiya/Desktop/janus_chs_model.vocabulary.* with mmap=None
2019-02-21 16:04:57,145 - gensim.utils - INFO - loading trainables recursively from C:/Users/aiya/Desktop/janus_chs_model.trainables.* with mmap=None
2019-02-21 16:04:57,155 - gensim.utils - INFO - setting ignored attribute cum_table to None
2019-02-21 16:04:57,215 - gensim.utils - INFO - loaded C:/Users/aiya/Desktop/janus_chs_model


In [54]:
from keras.layers import Embedding

EMBEDDING_DIM = 100 #词向量维度

embedding_layer = Embedding(len(embeddings_matrix),EMBEDDING_DIM,weights=[embeddings_matrix],trainable=False)


In [55]:
from keras.utils import plot_model
plot_model(embedding_layer, to_file='C:/Users/aiya/Desktop/model.png')

ImportError: Failed to import `pydot`. Please install `pydot`. For example with `pip install pydot`.

In [53]:
import tensorflow
logdir = "./logs/{}".format("C:/Users/aiya/Desktop/log")
tensorBoard = TensorBoard(log_dir = logdir,
                                    histogram_freq = 1,
                                    write_graph = True,
                                    write_images = False,
                                    embeddings_freq = 1,
                                    embeddings_layer_names = None,
                                    embeddings_metadata = None)


self.model.fit(train_x, train_y,
                       batch_size = self.batch_size,
                       epochs = self.epochs,
                       verbose = 1,
                       callbacks = [tensorBoard])

NameError: name 'TensorBoard' is not defined

In [56]:
#word2vec tensorboard
import tensorflow as tf
from tensorflow.contrib.tensorboard.plugins import projector
import numpy as np
import gensim

import warnings
warnings.filterwarnings(action='ignore',category=UserWarning,module='gensim')



In [57]:
fname = "C:/Users/aiya/Desktop/janus_chs_model"
model = gensim.models.KeyedVectors.load(fname)


2019-02-21 16:39:21,462 - gensim.utils - INFO - loading Word2VecKeyedVectors object from C:/Users/aiya/Desktop/janus_chs_model
2019-02-21 16:39:21,539 - gensim.utils - INFO - loading wv recursively from C:/Users/aiya/Desktop/janus_chs_model.wv.* with mmap=None
2019-02-21 16:39:21,552 - gensim.utils - INFO - setting ignored attribute vectors_norm to None
2019-02-21 16:39:21,556 - gensim.utils - INFO - loading vocabulary recursively from C:/Users/aiya/Desktop/janus_chs_model.vocabulary.* with mmap=None
2019-02-21 16:39:21,559 - gensim.utils - INFO - loading trainables recursively from C:/Users/aiya/Desktop/janus_chs_model.trainables.* with mmap=None
2019-02-21 16:39:21,559 - gensim.utils - INFO - setting ignored attribute cum_table to None
2019-02-21 16:39:21,592 - gensim.utils - INFO - loaded C:/Users/aiya/Desktop/janus_chs_model


In [58]:
max_size = len(model.wv.vocab)-1

In [60]:
w2v = np.zeros((max_size,model.layer1_size))

c:\users\aiya\appdata\local\programs\python\python36\lib\site-packages\ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `layer1_size` (Attribute will be removed in 4.0.0, use self.trainables.layer1_size instead).
  """Entry point for launching an IPython kernel.


In [61]:
w2v

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [ ]:
with open(".tsv",'w+') as file_metadata:
    for i,word in enumerate(model.wv.index2word[:max]):
        w2v[i] = modell.wv[word]
        file_metadata.write(word+'\n')
        

In [62]:
#word2vec tensorboard
import tensorflow as tf
from tensorflow.contrib.tensorboard.plugins import projector
import numpy as np
import gensim

import warnings
warnings.filterwarnings(action='ignore',category=UserWarning,module='gensim')


In [64]:
#w2v

model = gensim.models.Word2Vec.load("C:/Users/aiya/Desktop/janus_chs_model")
vocab = model.wv.vocab
word_vector = {}
for word in vocab:
	word_vector[word] = model[word]
print (word_vector)

2019-02-21 17:31:47,296 - gensim.utils - INFO - loading Word2Vec object from C:/Users/aiya/Desktop/janus_chs_model
2019-02-21 17:31:47,307 - gensim.utils - INFO - loading wv recursively from C:/Users/aiya/Desktop/janus_chs_model.wv.* with mmap=None
2019-02-21 17:31:47,313 - gensim.utils - INFO - setting ignored attribute vectors_norm to None
2019-02-21 17:31:47,341 - gensim.utils - INFO - loading vocabulary recursively from C:/Users/aiya/Desktop/janus_chs_model.vocabulary.* with mmap=None
2019-02-21 17:31:47,345 - gensim.utils - INFO - loading trainables recursively from C:/Users/aiya/Desktop/janus_chs_model.trainables.* with mmap=None
2019-02-21 17:31:47,349 - gensim.utils - INFO - setting ignored attribute cum_table to None
2019-02-21 17:31:47,351 - gensim.utils - INFO - loaded C:/Users/aiya/Desktop/janus_chs_model
c:\users\aiya\appdata\local\programs\python\python36\lib\site-packages\ipykernel_launcher.py:7: DeprecationWarning: Call to deprecated `__getitem__` (Method will be remove

{'微软': array([-2.41500931e-03, -7.20705139e-04,  3.86779360e-03, -4.17837128e-03,
        5.62714692e-03, -3.03825899e-03, -2.70294957e-03, -2.84309103e-03,
       -5.56905754e-04, -3.04424576e-03, -3.87800974e-03,  3.95978009e-03,
       -4.21393756e-03, -2.79402331e-04, -1.66395563e-03, -4.76947607e-04,
       -2.16551404e-03,  8.48994183e-04, -3.95935867e-03,  3.20912572e-03,
       -2.44042464e-03,  4.29926062e-04,  8.79490562e-03,  7.92667177e-03,
       -1.45037123e-03, -3.61663202e-04, -1.74634519e-03,  1.22663949e-03,
        2.55016354e-03,  6.02521934e-04, -4.26841155e-03,  4.17338032e-03,
        7.23533984e-03, -4.16344963e-03,  2.11651833e-03,  2.15596426e-03,
        5.99361723e-04,  3.38785676e-03, -8.65716953e-03, -3.16760666e-03,
        6.50625955e-03,  6.06573012e-04,  1.65285927e-03, -4.51834360e-03,
       -5.28343488e-03, -2.16281344e-03,  5.15595498e-03,  2.93581490e-03,
        6.54067704e-03,  7.21513899e-03, -1.85620028e-03, -2.20131828e-03,
       -5.58921229

In [65]:
sess = tf.InteractiveSession()

In [66]:
#Let us create a 2D tensor called embedding that holds our embeddings.
with tf.device("/cpu:0"):
    embedding = tf.Variable(w2v, trainable=False, name='embedding')


In [67]:
tf.global_variables_initializer().run()


In [68]:
path = 'tensorboard'



In [69]:
# let us create an object to Saver class which is actually used to 
#save and restore variables to and from our checkpoints
saver = tf.train.Saver()



In [70]:
# using file writer, we can save our summaries and events to our event file.
writer = tf.summary.FileWriter(path, sess.graph)


In [73]:
# adding into projector
config = projector.ProjectorConfig()
embed = config.embeddings.add()
embed.tensor_name = 'embedding'
#embed.metadata_path = 'metadata.tsv'



In [74]:

# Specify the width and height of a single thumbnail.
projector.visualize_embeddings(writer, config)

saver.save(sess, path+'/model.ckpt', global_step=max_size)



'tensorboard/model.ckpt-796'